In [1]:
!pip install tables

In [2]:
import tables
import numpy as np

In [3]:
properties=tables.open_file('trail_properties.h5')
print(properties)

trail_properties.h5 (File) ''
Last modif.: '2023-03-22T11:41:52+00:00'
Object Tree: 
/ (RootGroup) ''
/N_track (CArray(5451,)zlib(9)) ''
/avg_brightness (CArray(5451,)zlib(9)) ''
/duration (CArray(5451,)zlib(9)) ''
/max_brightness (CArray(5451,)zlib(9)) ''
/nrun (CArray(5451,)zlib(9)) ''
/start (CArray(5451,)zlib(9)) ''
/t0 (CArray(5451,)zlib(9)) ''
/time_in_night (CArray(5451,)zlib(9)) ''
/unique_pix (CArray(5451,)zlib(9)) ''
/velocity (CArray(5451,)zlib(9)) ''
/zenith (CArray(5451,)zlib(9)) ''



In [4]:
print(properties.root['N_track'].read())
print(properties.root['nrun'].read())

[-1. -1. -1. ...  0.  1.  0.]
[155172 155173 155174 ... 180349 180349 180379]


In [5]:
!pip install sshtunnel

In [6]:
import sys
import paramiko
import pandas as pd
import json
import sshtunnel
import mariadb
import sys
import paramiko
import datetime
from datetime import timedelta
import numpy as np
import math
import re

def getMdbCursor():
    conn = mariadb.connect(
        user="spencers",
        password="GieLope9ohquaep3xi",
        host='127.0.0.1',
        port=12345,
        database="HD_tables"
    )

    # Instantiate Cursor
    cur = conn.cursor()
    return cur

def load_collection(CMD):
    cur = getMdbCursor()
    print(CMD)
    cur.execute(CMD)
    df = pd.DataFrame(cur.fetchall())
    column_title = re.search('SELECT(.*)FROM', CMD)
    df.columns = list(column_title.group(1).replace(" ", "").split(","))
    return df

def getCollForStat(col):
    allCols = getMdbCursor()
    allCols.execute('SHOW COLUMNS FROM '+ 'HD_test'+'.'+col)
    cols = allCols.fetchall()

    list_allCols = []
    for i in  range(len(cols)):
        list_allCols = list_allCols + [cols[i][0]]
    list_allCols_str =  ','.join(list_allCols[1:])
    cur = getMdbCursor()
    CMD = "SELECT " + list_allCols_str +" FROM HD_test."+col+" WHERE Run > 100 ORDER BY HD_test."+col+".WhenEntered asc"
    cur.execute(CMD)
    df = pd.DataFrame(cur.fetchall())
    df_atm =  df
    df_atm.columns = list_allCols[1:]
    #df_atm = df_atm.drop_duplicates(['Run','Telescope'],keep='last')

    df_atm =df_atm.merge(df_run, on=['Run'])

    df_atm['Year'] = [e.year  for e in list(df_atm['TimeOfStart'])]
    df_atm['Month'] = [e.month  for e in list(df_atm['TimeOfStart'])]
    df_atm['doy'] = [e.timetuple().tm_yday for e in list(df_atm['TimeOfStart'])]
    df_atm['Nrun']=1
    df_atm.groupby(['Month']).sum()
    return df_atm


CMD = "SELECT Run, Target_Name FROM  HD_test.Monitor_Run_Analysis"
df_run = load_collection(CMD)
df_run.columns = ['Run', 'Target']
df_run = df_run.drop_duplicates(['Run'],keep='last')
print(df_run)

SELECT Run, Target_Name FROM  HD_test.Monitor_Run_Analysis
           Run                    Target
803      52021            HESS J1503-582
1341     23707               Vela Junior
1343     23709               Vela Junior
1599     54296              1ES 0414+009
1600     54295              1ES 0414+009
...        ...                       ...
179047  173680            PSR J1509-5850
179048  173702  SDSS J143016.05+230344.4
179049  173667            PMN J0948+0022
179050  173705  SDSS J143016.05+230344.4
179051  173704  SDSS J143016.05+230344.4

[50535 rows x 2 columns]


In [7]:
tracks=properties.root['N_track'].read()+1
nrun=properties.root['nrun'].read()
df_tracks=pd.DataFrame({'Run':nrun,'Tracks':tracks})
print(df_tracks)

         Run  Tracks
0     155172     0.0
1     155173     0.0
2     155174     0.0
3     155179     0.0
4     155246     0.0
...      ...     ...
5446  180348     4.0
5447  180348     5.0
5448  180349     1.0
5449  180349     2.0
5450  180379     1.0

[5451 rows x 2 columns]


In [8]:
df_tracks=df_tracks.merge(df_run,left_on='Run',right_on='Run')
print(df_tracks)

         Run  Tracks              Target
0     155172     0.0  Fornax A east lobe
1     155173     0.0  Fornax A east lobe
2     155174     0.0  Fornax A east lobe
3     155179     0.0        PKS 0625-354
4     155246     0.0  Fornax A east lobe
...      ...     ...                 ...
5445  180348     4.0           AT2023aub
5446  180348     5.0           AT2023aub
5447  180349     1.0           AT2023aub
5448  180349     2.0           AT2023aub
5449  180379     1.0           AT2023aub

[5450 rows x 3 columns]


In [9]:
df_backup=df_tracks.copy(deep=True)
df_tracks=df_tracks[df_tracks['Tracks']!=0]
print(df_tracks)
print(df_tracks['Target'].unique())

         Run  Tracks        Target
6     155336     1.0  PKS 0625-354
10    155398     1.0  PKS 0625-354
15    155982     1.0  PKS 2155-304
16    155982     2.0  PKS 2155-304
17    155983     1.0  PKS 2155-304
...      ...     ...           ...
5445  180348     4.0     AT2023aub
5446  180348     5.0     AT2023aub
5447  180349     1.0     AT2023aub
5448  180349     2.0     AT2023aub
5449  180379     1.0     AT2023aub

[1658 rows x 3 columns]
['PKS 0625-354' 'PKS 2155-304' 'ToO 938899' 'ToO PKS 0208-512'
 'LMC 2019 Pos. 4' '3C 273' '4FGL J1405.1-6119' 'ToO200306' 'Vela Pulsar'
 'Inner Galaxy Survey pos 3-6' 'Inner Galaxy Survey pos 3-5'
 'Inner Galaxy Survey pos 3-7' 'Inner Galaxy Survey pos 2-8'
 'Inner Galaxy Survey pos 2-5' 'Inner Galaxy Survey pos 2-6'
 'Inner Galaxy Survey pos 1-5' 'ToO PKS 0903-57' 'Sgr A*' 'ToO200427'
 'Inner Galaxy Survey pos 3-8' 'ToO200503' 'HESS J1832-093' 'Cen A' 'None'
 'ToO PKS 1156-221' 'ToO200616' 'SS 433 p3' 'Kepler SNR' 'eHWC J2019+368'
 'PSR J1413-6205

In [10]:
import matplotlib.pyplot as plt
replace_values = {'Geminga Monogem P1' : 'Geminga Monogem', 'Geminga Monogem P2' : 'Geminga Monogem' ,'Geminga Monogem P3':'Geminga Monogem' ,
                  'Geminga Monogem P4' : 'Geminga Monogem', 'Geminga Monogem P5' : 'Geminga Monogem', 'Geminga Monogem P6' : 'Geminga Monogem',
                  'Geminga Monogem P7' : 'Geminga Monogem', 'Geminga Monogem P8' : 'Geminga Monogem','Inner Galaxy Survey pos 3-6': 'Inner Galaxy Survey',
                  'Inner Galaxy Survey pos 3-5':'Inner Galaxy Survey','Inner Galaxy Survey pos 3-7': 'Inner Galaxy Survey','Inner Galaxy Survey pos 3-5': 'Inner Galaxy Survey',
                  'Inner Galaxy Survey pos 3-7': 'Inner Galaxy Survey', 'Inner Galaxy Survey pos 2-8': 'Inner Galaxy Survey','Inner Galaxy Survey pos 2-5': 'Inner Galaxy Survey',
                  'Inner Galaxy Survey pos 2-6': 'Inner Galaxy Survey','Inner Galaxy Survey pos 1-5': 'Inner Galaxy Survey', 'Inner Galaxy Survey pos 3-8': 'Inner Galaxy Survey',
                  'Crab Nebula 55-60deg off1.5':'Crab Nebula', 'Crab Nebula 55-60deg off1.0':'Crab Nebula','Crab Nebula 50-55deg off1.0':'Crab Nebula',
                  'SS 433 p3':'SS 433','SS 433 p1':'SS 433','SS 433 Q2':'SS 433','SS 433 Q1':'SS 433','SS 433 Q3':'SS 433','SS 433 Q4':'SS 433','LMC 2019 Pos. 4':'LMC'}                                                                               

df_tracks = df_tracks.replace({"Target": replace_values})
df_backup = df_backup.replace({"Target": replace_values})
'''
df_tracks['Target'][df_tracks.Target.str.contains('Geminga Monogem')] = 'Geminga Monogem'
df_tracks=df_tracks.copy(deep=True)
df_tracks['Target'][df_tracks.Target.str.contains('Inner Galactic Survey')] = 'Inner Galactic Survey'
#df_tracks['Target'][df_tracks.Target.str.contains('Crab Nebula')] = 'Crab Nebula'
#df_tracks['Target'][df_tracks.Target.str.contains('SS 433')] = 'SS 433'
'''

#df_tracks=df_tracks[df.loc[df['Target'].str.contains('Geminga Monogem'), 'Target'] = 'Geminga Monogem']
print(df_tracks['Target'].unique())
df_tracks.groupby('Target').Tracks.sum().plot.barh(figsize=(100,80),fontsize=30,ylabel='',xlabel='')
plt.savefig('Targetlist.png')

['PKS 0625-354' 'PKS 2155-304' 'ToO 938899' 'ToO PKS 0208-512' 'LMC'
 '3C 273' '4FGL J1405.1-6119' 'ToO200306' 'Vela Pulsar'
 'Inner Galaxy Survey' 'ToO PKS 0903-57' 'Sgr A*' 'ToO200427' 'ToO200503'
 'HESS J1832-093' 'Cen A' 'None' 'ToO PKS 1156-221' 'ToO200616' 'SS 433'
 'Kepler SNR' 'eHWC J2019+368' 'PSR J1413-6205' 'ToO MGAB-V207'
 '3FGL J0209.4-5229' 'HESS J1731-347 center' 'HESS J1731-347'
 'Crab Nebula' 'Pictor A' 'ToO IC200926' 'ToO BL Lac'
 'ToO IceCube-201007A' 'ToO201010' 'ToO IceCube-201114A' 'ToO PKS0514-459'
 'ToO PKS 0514-459' 'PSR B1259-63' 'ToO PKS 1127-14' 'ToO PKS 0837+012'
 '4FGL J1723.5-0501e' 'PKS 1510-089' 'ToO210411' 'PSR B1706-44'
 'FHES J1208.7-5229' 'ToO GB6 J1058+2817' 'Bania Clump 2'
 'ToO PKS B0027-426' 'GRB_ToO210521A' 'ToO PKS 1313-333'
 'FHES J1741.6-3917' 'GRB_ToO210619' 'M 87' 'GRB_ToO210702'
 'SNR G330.2+01.0' 'GRB_ToO210708' 'ToO PKS 1334-127' 'PKS 1334-127'
 'GRB_ToO210802A' '1ES 0229+200' 'ToO RS Ophiuchi' 'GRB_ToO210901'
 '3C 120' 'ToO SN 2021yja'

In [11]:
pd.set_option('display.max_rows', None,
                       'display.max_columns', None,
                       'display.precision', 3,
                       )
df_tracks.groupby('Target').Tracks.sum()

Target
1ES 0229+200                 43.0
1RXS J195815.6-301119         1.0
3C 120                       31.0
3C 273                        1.0
3FGL J0209.4-5229             9.0
3FHL J0543.9-5532            17.0
4FGL J0022.0+0006            85.0
4FGL J0039.1-2219             8.0
4FGL J0622.3-2605            21.0
4FGL J1405.1-6119            11.0
4FGL J1714.0-2029             1.0
4FGL J1723.5-0501e           94.0
AT2023aub                    20.0
Bania Clump 2                 3.0
Cen A                        39.0
Crab Nebula                  67.0
FHES J1208.7-5229           100.0
FHES J1741.6-3917             6.0
Fornax A                     54.0
GC pos 2                      6.0
GRB211106A                    2.0
GRB_ToO210521A                1.0
GRB_ToO210619                 1.0
GRB_ToO210702                12.0
GRB_ToO210708                 3.0
GRB_ToO210802A                1.0
GRB_ToO210901                 3.0
GRB_ToO211207                14.0
GRB_ToO220305                 7.0
GRB_ToO

In [16]:
print(df_tracks[df_tracks.Target.str.contains('ToO')].Tracks.sum())
print(df_tracks.Tracks.sum())

492.0
2953.0


In [20]:
print(len(df_backup[df_backup.Target.str.contains('ToO')].Run))
print(len(df_backup.Run))

923
5450


In [22]:
923/5450

0.1693577981651376

In [23]:
492/2953

0.1666102268879106

In [19]:
print(248.0/1295.0)

0.1915057915057915


In [14]:
df_tracks2=df_tracks.copy(deep=True)
df_tracks2['Target'][df_tracks2.Target.str.contains('ToO')] = 'ToO'
print(df_tracks2['Target'].unique())
df_tracks2.groupby('Target').Tracks.sum().plot.barh(figsize=(100,80),fontsize=30,ylabel='',xlabel='')
plt.savefig('Targetlisttoo.png')

['PKS 0625-354' 'PKS 2155-304' 'ToO' 'LMC' '3C 273' '4FGL J1405.1-6119'
 'Vela Pulsar' 'Inner Galaxy Survey' 'Sgr A*' 'HESS J1832-093' 'Cen A'
 'None' 'SS 433' 'Kepler SNR' 'eHWC J2019+368' 'PSR J1413-6205'
 '3FGL J0209.4-5229' 'HESS J1731-347 center' 'HESS J1731-347'
 'Crab Nebula' 'Pictor A' 'PSR B1259-63' '4FGL J1723.5-0501e'
 'PKS 1510-089' 'PSR B1706-44' 'FHES J1208.7-5229' 'Bania Clump 2'
 'FHES J1741.6-3917' 'M 87' 'SNR G330.2+01.0' 'PKS 1334-127'
 '1ES 0229+200' '3C 120' 'GRB211106A' 'Geminga Monogem' 'Puppis A NE'
 'PSR J1509-5850' 'PSR J0940-5428' 'PMN J0948+0022'
 'SDSS J143016.05+230344.4' '1RXS J195815.6-301119' 'PKS 1502+036'
 '4FGL J1714.0-2029' '4FGL J0039.1-2219' 'Fornax A' 'V4641 Sgr' 'GC pos 2'
 'MAXI J1848-015' '4FGL J0022.0+0006' '3FHL J0543.9-5532'
 '4FGL J0622.3-2605' 'AT2023aub']


/tmp/ipykernel_85667/4204221425.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_tracks2['Target'][df_tracks2.Target.str.contains('ToO')] = 'ToO'


In [15]:
print(df_tracks['Target'].unique())
(df_backup.groupby('Target').Run.sum()).plot.barh(figsize=(100,80),fontsize=30,ylabel='',xlabel='')
plt.savefig('Targetlistnorm.png')

['PKS 0625-354' 'PKS 2155-304' 'ToO 938899' 'ToO PKS 0208-512' 'LMC'
 '3C 273' '4FGL J1405.1-6119' 'ToO200306' 'Vela Pulsar'
 'Inner Galaxy Survey' 'ToO PKS 0903-57' 'Sgr A*' 'ToO200427' 'ToO200503'
 'HESS J1832-093' 'Cen A' 'None' 'ToO PKS 1156-221' 'ToO200616' 'SS 433'
 'Kepler SNR' 'eHWC J2019+368' 'PSR J1413-6205' 'ToO MGAB-V207'
 '3FGL J0209.4-5229' 'HESS J1731-347 center' 'HESS J1731-347'
 'Crab Nebula' 'Pictor A' 'ToO IC200926' 'ToO BL Lac'
 'ToO IceCube-201007A' 'ToO201010' 'ToO IceCube-201114A' 'ToO PKS0514-459'
 'ToO PKS 0514-459' 'PSR B1259-63' 'ToO PKS 1127-14' 'ToO PKS 0837+012'
 '4FGL J1723.5-0501e' 'PKS 1510-089' 'ToO210411' 'PSR B1706-44'
 'FHES J1208.7-5229' 'ToO GB6 J1058+2817' 'Bania Clump 2'
 'ToO PKS B0027-426' 'GRB_ToO210521A' 'ToO PKS 1313-333'
 'FHES J1741.6-3917' 'GRB_ToO210619' 'M 87' 'GRB_ToO210702'
 'SNR G330.2+01.0' 'GRB_ToO210708' 'ToO PKS 1334-127' 'PKS 1334-127'
 'GRB_ToO210802A' '1ES 0229+200' 'ToO RS Ophiuchi' 'GRB_ToO210901'
 '3C 120' 'ToO SN 2021yja'